In [1]:
import datetime
import nltk
import matplotlib.pyplot as plt
import matplotlib as mpl
import seaborn as sns
import pandas as pd
import numpy as np
import time
import math
import sys
import gensim
import os
import warnings
import torch
import itertools
import multiprocessing as mp
from collections import Counter, defaultdict
from inspect import signature
from scipy.stats import ks_2samp, hypergeom
from sklearn.metrics import precision_recall_curve, f1_score, auc
from sklearn.model_selection import train_test_split, KFold
from scipy import spatial, stats
from statsmodels.sandbox.stats.multicomp import multipletests
from nltk.corpus import brown
from nltk.tokenize import word_tokenize, sent_tokenize
from sklearn.neighbors import KNeighborsClassifier
from pytorch_pretrained_bert import BertTokenizer, BertModel, BertForMaskedLM
from gensim.parsing.preprocessing import strip_non_alphanum, stem_text, preprocess_string, remove_stopwords
from gensim.utils import simple_preprocess
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.decomposition import NMF
from sklearn.decomposition import LatentDirichletAllocation as LDA
from sklearn.cluster import AgglomerativeClustering

sys.path.append("../../oats")
from oats.utils.utils import save_to_pickle, load_from_pickle, merge_list_dicts, flatten, to_hms
from oats.utils.utils import function_wrapper_with_duration
from oats.biology.dataset import Dataset
from oats.biology.groupings import Groupings
from oats.biology.relationships import ProteinInteractions, AnyInteractions
from oats.annotation.ontology import Ontology
from oats.annotation.annotation import annotate_using_noble_coder
from oats.distances import pairwise as pw
from oats.distances.edgelists import merge_edgelists, make_undirected, remove_self_loops, subset_with_ids

mpl.rcParams["figure.dpi"] = 400
warnings.simplefilter('ignore')
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)
nltk.download('punkt', quiet=True)
nltk.download('brown', quiet=True)
nltk.download('averaged_perceptron_tagger', quiet=True)

True

In [2]:
o = Ontology("../../oats/tests/data/test_ontology.obo")
for k,v in o.subclass_dict.items():
    print(k,v)

TO:0000001 []
TO:0000002 ['TO:0000001']
TO:0000003 ['TO:0000001']
TO:0000004 ['TO:0000002', 'TO:0000003', 'TO:0000001']
TO:0000005 ['TO:0000004', 'TO:0000002', 'TO:0000003', 'TO:0000001']
TO:0000006 ['TO:0000004', 'TO:0000002', 'TO:0000003', 'TO:0000001']
TO:0000007 ['TO:0000001']
TO:0000008 ['TO:0000007', 'TO:0000001']
TO:0000009 ['TO:0000008', 'TO:0000007', 'TO:0000001']


In [28]:
import pronto
pronto_o = pronto.Ontology("../ontologies/go-basic.obo")
print("done")
for t in pronto_o.terms():
    print(t.name)
    if (t.name is not None) and ("obsolete" not in t.name):    
        print(t.name)
        #pass
    else:
        print("HERE")

#import pronto
#pronto_o = pronto.Ontology("../ontologies/po.obo")

#term = pronto_o["PO:0000003"]

#for term in pronto_o.terms():
#sup = [t for t in term.subclasses(distance=1)]
#print(sup)
#break

done
mitochondrion inheritance
mitochondrion inheritance
mitochondrial genome maintenance
mitochondrial genome maintenance
reproduction
reproduction
obsolete ribosomal chaperone activity
HERE
high-affinity zinc transmembrane transporter activity
high-affinity zinc transmembrane transporter activity
low-affinity zinc ion transmembrane transporter activity
low-affinity zinc ion transmembrane transporter activity
obsolete thioredoxin
HERE
alpha-1,6-mannosyltransferase activity
alpha-1,6-mannosyltransferase activity
trans-hexaprenyltranstransferase activity
trans-hexaprenyltranstransferase activity
vacuole inheritance
vacuole inheritance
single strand break repair
single strand break repair
single-stranded DNA endodeoxyribonuclease activity
single-stranded DNA endodeoxyribonuclease activity
phosphopyruvate hydratase complex
phosphopyruvate hydratase complex
lactase activity
lactase activity
alpha-glucoside transport
alpha-glucoside transport
regulation of DNA recombination
regulation of DN

positive regulation of defense response to virus by host
positive regulation of defense response to virus by host
detection of oomycetes
detection of oomycetes
leukocyte chemotaxis involved in inflammatory response
leukocyte chemotaxis involved in inflammatory response
leukocyte chemotaxis involved in immune response
leukocyte chemotaxis involved in immune response
detection of endoplasmic reticulum overloading
detection of endoplasmic reticulum overloading
detection of unfolded protein
detection of unfolded protein
detection of misfolded protein
detection of misfolded protein
response to molecule of bacterial origin
response to molecule of bacterial origin
response to molecule of fungal origin
response to molecule of fungal origin
response to oomycetes
response to oomycetes
response to molecule of oomycetes origin
response to molecule of oomycetes origin
response to parasitic plant
response to parasitic plant
defense response to parasitic plant
defense response to parasitic plant
dete

obsolete protein C (activated) activity
HERE
obsolete thrombin activity
HERE
protein-glutamine gamma-glutamyltransferase activity
protein-glutamine gamma-glutamyltransferase activity
obsolete complement activity
HERE
obsolete alternative-complement-pathway C3/C5 convertase activity
HERE
obsolete classical-complement-pathway C3/C5 convertase activity
HERE
obsolete complement component C1r activity
HERE
obsolete complement component C1s activity
HERE
obsolete complement factor D activity
HERE
obsolete complement factor I activity
HERE
obsolete major histocompatibility complex antigen
HERE
obsolete class I major histocompatibility complex antigen
HERE
obsolete class II major histocompatibility complex antigen
HERE
obsolete MHC-interacting protein
HERE
antigen binding
antigen binding
catalytic activity
catalytic activity
alpha,alpha-trehalose-phosphate synthase (UDP-forming) activity
alpha,alpha-trehalose-phosphate synthase (UDP-forming) activity
alpha-ketoacid dehydrogenase activity
alpha

RNA polymerase III complex
RNA polymerase III complex
transcription factor complex
transcription factor complex
RNA polymerase transcription factor SL1 complex
RNA polymerase transcription factor SL1 complex
transcription factor TFIID complex
transcription factor TFIID complex
obsolete transcription-activating factor, 30kD
HERE
Ada2/Gcn5/Ada3 transcription activator complex
Ada2/Gcn5/Ada3 transcription activator complex
transcription factor TFIIA complex
transcription factor TFIIA complex
transcription factor TFIIE complex
transcription factor TFIIE complex
transcription factor TFIIF complex
transcription factor TFIIF complex
transcription factor TFIIH holo complex
transcription factor TFIIH holo complex
chromatin silencing complex
chromatin silencing complex
obsolete chromatin assembly complex
HERE
anaphase-promoting complex
anaphase-promoting complex
spliceosomal complex
spliceosomal complex
U5 snRNP
U5 snRNP
U7 snRNP
U7 snRNP
U2-type spliceosomal complex
U2-type spliceosomal complex

pole plasm protein localization
pole plasm protein localization
negative regulation of oskar mRNA translation
negative regulation of oskar mRNA translation
insemination
insemination
sperm displacement
sperm displacement
peptide pheromone maturation
peptide pheromone maturation
positive regulation of transcription from RNA polymerase II promoter by pheromones
positive regulation of transcription from RNA polymerase II promoter by pheromones
obsolete bilateral process
HERE
obsolete unilateral process
HERE
single fertilization
single fertilization
binding of sperm to zona pellucida
binding of sperm to zona pellucida
acrosome reaction
acrosome reaction
penetration of zona pellucida
penetration of zona pellucida
fusion of sperm to egg plasma membrane involved in single fertilization
fusion of sperm to egg plasma membrane involved in single fertilization
egg activation
egg activation
pronuclear fusion
pronuclear fusion
obsolete embryogenesis and morphogenesis
HERE
regulation of mitotic cell 

...

isovaleryl-CoA(4-) metabolic process
isovaleryl-CoA(4-) metabolic process
isovaleryl-CoA(4-) catabolic process
isovaleryl-CoA(4-) catabolic process
isovaleryl-CoA(4-) biosynthetic process
isovaleryl-CoA(4-) biosynthetic process
3-methylbut-2-enoyl-CoA(4-) metabolic process
3-methylbut-2-enoyl-CoA(4-) metabolic process
3-methylbut-2-enoyl-CoA(4-) catabolic process
3-methylbut-2-enoyl-CoA(4-) catabolic process
3-methylbut-2-enoyl-CoA(4-) biosynthetic process
3-methylbut-2-enoyl-CoA(4-) biosynthetic process
negative regulation of bacterial-type flagellum-dependent cell motility
negative regulation of bacterial-type flagellum-dependent cell motility
regulation of hepatocyte growth factor receptor signaling pathway
regulation of hepatocyte growth factor receptor signaling pathway
negative regulation of hepatocyte growth factor receptor signaling pathway
negative regulation of hepatocyte growth factor receptor signaling pathway
positive regulation of hepatocyte growth factor receptor signali

regulation of protein tyrosine phosphatase activity
negative regulation of protein tyrosine phosphatase activity
negative regulation of protein tyrosine phosphatase activity
positive regulation of protein tyrosine phosphatase activity
positive regulation of protein tyrosine phosphatase activity
MAPK cascade involved in axon regeneration
MAPK cascade involved in axon regeneration
positive regulation of mitotic cytokinesis, site selection
positive regulation of mitotic cytokinesis, site selection
regulation of transdifferentiation
regulation of transdifferentiation
negative regulation of transdifferentiation
negative regulation of transdifferentiation
positive regulation of transdifferentiation
positive regulation of transdifferentiation
protein localization to photoreceptor connecting cilium
protein localization to photoreceptor connecting cilium
regulation of RNA polymerase III activity
regulation of RNA polymerase III activity
negative regulation of RNA polymerase III activity
negativ

calcium-induced calcium release activity involved in regulation of presynaptic cytosolic calcium ion concentration
calcium:cation antiporter activity involved in regulation of presynaptic cytosolic calcium ion concentration
calcium:cation antiporter activity involved in regulation of presynaptic cytosolic calcium ion concentration
calcium-transporting ATPase activity involved in regulation of presynaptic cytosolic calcium ion concentration
calcium-transporting ATPase activity involved in regulation of presynaptic cytosolic calcium ion concentration
voltage-gated calcium channel activity involved in regulation of postsynaptic cytosolic calcium levels
voltage-gated calcium channel activity involved in regulation of postsynaptic cytosolic calcium levels
calcium-induced calcium release activity involved in regulation of postsynaptic cytosolic calcium ion concentration
calcium-induced calcium release activity involved in regulation of postsynaptic cytosolic calcium ion concentration
calcium

mitochondrial L-ornithine transmembrane transport
G protein-coupled glucose receptor activity
G protein-coupled glucose receptor activity
C-terminal protein demethylation
C-terminal protein demethylation
perinuclear endoplasmic reticulum membrane
perinuclear endoplasmic reticulum membrane
peptidyl-serine trans-autophosphorylation
peptidyl-serine trans-autophosphorylation
regulation of cytoplasmic translational termination
regulation of cytoplasmic translational termination
obsolete lysosome lysis
HERE
obsolete intracellular membrane-bounded organelle binding
HERE
phospholipase D activator activity
phospholipase D activator activity
cardiac Troponin complex
cardiac Troponin complex
hydroxyproline O-arabinosyltransferase activity
hydroxyproline O-arabinosyltransferase activity
divisome complex
divisome complex
FtsQBL complex
FtsQBL complex
FtsBL complex
FtsBL complex
ATF4-CREB1 transcription factor complex
ATF4-CREB1 transcription factor complex
ATF1-ATF4 transcription factor complex
ATF

negative regulation of cellular response to X-ray
positive regulation of cellular response to X-ray
positive regulation of cellular response to X-ray
obsolete regulation of rubidium ion transmembrane transporter activity
HERE
obsolete negative regulation of rubidium ion transmembrane transporter activity
HERE
obsolete positive regulation of rubidium ion transmembrane transporter activity
HERE
actomyosin contractile ring assembly actin filament organization
actomyosin contractile ring assembly actin filament organization
regulation of cardiac muscle cell myoblast differentiation
regulation of cardiac muscle cell myoblast differentiation
negative regulation of cardiac muscle cell myoblast differentiation
negative regulation of cardiac muscle cell myoblast differentiation
negative regulation of seed maturation
negative regulation of seed maturation
positive regulation of seed maturation
positive regulation of seed maturation
regulation of phragmoplast microtubule organization
regulation o

In [18]:
for t in pronto_o.terms():
    for s in t.synonyms:
        print(s.description)

velocity
relative color
colour
color lightness
color intensity
color value
compositionality
structure, composition
composed of
content
concentration
firmness
toughness
impenetrability
relational shape quality
nutritional quality
temporal
incidence
parental type
pattern
distribution
number
count in organism
quantitative
presence or absence in organism
presence
responsivity
response
reactivity
sensitivity
amount of rotation
angular placement
plane angle
angle
angular magnitude
placement
relational spatial quality
location
relational structural quality
conformation
behavioural quality
propensity to consume
litter size
incomplete
abolished
fixed
fast speed
high speed
slow
slow speed
whitish
dark
dull
pale
blotched
mottled (sensu Drosophila)
pigmented
unpigmented
long distance
short distance
high frequency
frequent
low frequency
infrequent
tough
impenetrable
firm
ramified
ramiform
helicoid
helical
helicoidal
spiral
helix-shaped
curled
bowing
plate-like
oblate spheroid
of a leaf shape
feathe